In [1]:
import xml.etree.ElementTree as ET
import itertools

In [2]:
#path_inco = "/home/ziane212/crisco_work/ressources/11_1502_Roche-Guyon-inconnu.txt"
path_presto = "/home/ziane212/crisco_work_ressources/dico_PRESTO_SIMPLE_10.01.23.dff"
path_corrTable = "/home/ziane212/crisco_work_ressources/MICLE_CorrTable_13-02-23.csv"

path_in = "/home/ziane212/crisco_work/ressources/1487_cronicque/1487_Cronicque_parsed_SRCMF-flau_15-02-23.xml"             
path_out = "/home/ziane212/crisco_work/ressources/1487_cronicque/1487_Cronicque_lemmatised_15-02-23.xml"                


In [3]:
#création du dictionnaire python à partir du dictionnaire PRESTO
PRESTO = open(path_presto, encoding='utf-8')

#parsing du fichier .dff et création du dictionnaire python
dict_PRESTO = {}
for entry in PRESTO:
    entry = entry.rstrip("\n")
    entry = entry.split("/")
    if entry[0] in dict_PRESTO:
        # nouvelle valeur si l'entrée est déjà dans le dictionnaire python
        dict_PRESTO[entry[0]].append(entry)
    else:
        # nouvelle entrée dans le dictionnaire python
        dict_PRESTO[entry[0]] = [entry]
        
PRESTO.close()

In [4]:
#création du dictionnaire python à partir de la table de conversion
CorrTable = open(path_corrTable, encoding='utf-8')
dict_CorrTable = {}
for i in CorrTable:
    i = i.split(",")
    if i[4] in dict_CorrTable:
        dict_CorrTable[i[4]].append(i)
    else:
        dict_CorrTable[i[4]]=[i]
        
CorrTable.close()

In [5]:
def lemmatisation(entry, list_lemma):
    if entry[1] == tag[1]:
        if entry[1] in list_prpos:
            pass
        else:
            list_prpos.append(entry[1])

        if entry[2] in list_prfeat:
            pass
        else:
            list_prfeat.append(entry[2])

        for prfeat, prpos in zip(list_prfeat, itertools.cycle(list_prpos)):
            if entry[1] == prpos and entry[2] == prfeat:
                list_lemma.append(entry[3].lower())
                
    

In [6]:
list_inco = []
nb_sent = 0
cnt = 0
tree = ET.parse(open(path_in, encoding='utf-8'))
root = tree.getroot()

for w in root.findall('.//w'):

    # lecture des tokens
    token = w.text
    
    # edit token (lower pour eviter les majuscules en début de phrase, rstrip pour éviter les points agglutinés sur le token)
    token = token.replace('[', '').replace('(', '').replace(']', '').replace(')', '').rstrip('-')
    if token.endswith('.') and len(token)!=1:
        token = token.replace('.', '')
    
    token = token.lower()

    # edit lemme
    s_udpos = w.get('udpos')
            
    list_prpos = []
    list_prfeat = []
    list_lemma = []
    #dev 
    print(token)
    #dev 
    print(s_udpos)
    # test de matching dans le dictionnaire
    if token in dict_PRESTO.keys():
        # résolution de l'ambiguité en comparant l'étiquette POS UD avec celle dans le dictionnaire PRESTO
        if len(dict_PRESTO[token]) != 1: # si plusieurs valeurs pour une entrée dans le dictionnaire alors ambiguité
            for entry in dict_PRESTO[token]: # itération des valeurs pour l'entrée
                for tag in dict_CorrTable[s_udpos]:
                    lemmatisation(entry, list_lemma)

        else:
            for tag in dict_CorrTable[s_udpos]:
                lemmatisation(dict_PRESTO[token][0], list_lemma)
    
    # absence du verbe dans presto
    else:
        w.attrib['NoMatchingPresto'] = 'Word'
    
    list_lemma = list(sorted(set(list_lemma)))
    
    print(list_lemma)
    if list_lemma != []:

        if len(list_lemma) > 1:
            s_lemma = '///'.join(list_lemma)
        else:
            s_lemma = list_lemma[0]

        # Gestion de l'absence de conversion de l'étiquette UPenn
        try:
            w.attrib['lemma'] = s_lemma
        except NameError:
            s_lemma = '_'
            w.attrib['lemma'] = s_lemma
        
    
    elif list_lemma == [] and w.get('NoMatchingPresto')!='Word':
        
        if s_udpos=='PROPN':
            s_lemma = w.text
            w.attrib['lemma'] = s_lemma
        else:
            s_lemma = '_'
            w.attrib['lemma'] = s_lemma

            w.attrib['NoMatchingPresto'] = 'POS'
            
    elif list_lemma == [] and w.get('NoMatchingPresto')=='Word':
        
        if s_udpos=='PROPN':
            s_lemma = w.text
            w.attrib['lemma'] = s_lemma
            w.attrib.pop('NoMatchingPresto')
        else:
            s_lemma = '_'
            w.attrib['lemma'] = s_lemma
            
            
    
    print(w.attrib)
    #del s_lemma        
        

aprez
ADV
['après']
{'n': '1', 'udpos': 'ADV', 'lemma': 'après', 'head': '57', 'function': 'advmod', 'join': '_', 'retagging': 'ADV'}
que
SCONJ
['que']
{'n': '2', 'udpos': 'SCONJ', 'lemma': 'que', 'head': '9', 'function': 'mark', 'join': '_', 'retagging': 'SCONJ'}
le
DET
['le']
{'n': '3', 'udpos': 'DET', 'lemma': 'le', 'head': '4', 'function': 'det', 'join': '_', 'retagging': 'DET'}
roy
NOUN
['roi', 'rois']
{'n': '4', 'udpos': 'NOUN', 'lemma': 'roi///rois', 'head': '9', 'function': 'nsubj', 'join': '_', 'retagging': 'NOUN'}
philippe de france
PROPN
[]
{'n': '5', 'udpos': 'PROPN', 'lemma': 'Philippe de France', 'head': '4', 'function': 'flat', 'join': '_', 'retagging': 'PROPN'}
surnommé
VERB
['surnommer']
{'n': '6', 'udpos': 'VERB', 'lemma': 'surnommer', 'head': '9', 'function': 'advcl', 'join': '_', 'retagging': 'VERB'}
auguste
PROPN
['auguste']
{'n': '7', 'udpos': 'PROPN', 'lemma': 'auguste', 'head': '4', 'function': 'flat', 'join': '_', 'retagging': 'PROPN'}
eut
AUX
['avoir']
{'n': '

de
ADP
['de']
{'n': '26', 'udpos': 'ADP', 'lemma': 'de', 'head': '27', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
navarre
PROPN
['navarre']
{'n': '27', 'udpos': 'PROPN', 'lemma': 'navarre', 'head': '25', 'function': 'flat', 'join': '_', 'retagging': 'PROPN'}
,
PUNCT
[',', '.', '_']
{'n': '28', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '29', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
jehan
PROPN
['jean']
{'n': '29', 'udpos': 'PROPN', 'lemma': 'jean', 'head': '13', 'function': 'conj', 'join': '_', 'retagging': 'PROPN'}
,
PUNCT
[',', '.', '_']
{'n': '30', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '31', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
conte
NOUN
['comte', 'comté', 'conte', 'conté']
{'n': '31', 'udpos': 'NOUN', 'lemma': 'comte///comté///conte///conté', 'head': '29', 'function': 'appos', 'join': '_', 'retagging': 'NOUN'}
de
ADP
['de']
{'n': '32', 'udpos': 'ADP', 'lemma': 'de', 'head': '33', 'function': 'case', 'join': '_', 'retagging

{'n': '21', 'udpos': 'DET', 'lemma': 'le', 'head': '22', 'function': 'det', 'join': '_', 'retagging': 'DET'}
duché
NOUN
['duché']
{'n': '22', 'udpos': 'NOUN', 'lemma': 'duché', 'head': '19', 'function': 'obj', 'join': '_', 'retagging': 'NOUN'}
,
PUNCT
[',', '.', '_']
{'n': '23', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '22', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
réservé
ADP
[]
{'n': '24', 'udpos': 'ADP', 'lemma': '_', 'head': '22', 'function': 'case', 'join': '_', 'retagging': 'ADP', 'NoMatchingPresto': 'POS'}
le
DET
['le']
{'n': '25', 'udpos': 'DET', 'lemma': 'le', 'head': '26', 'function': 'det', 'join': '_', 'retagging': 'DET'}
mont-sainct-michiel
PROPN
[]
{'n': '26', 'udpos': 'PROPN', 'lemma': 'Mont-Sainct-Michiel', 'head': '32', 'function': 'nmod', 'join': '_', 'retagging': 'NOUN'}
;
PUNCT
[';', '_']
{'n': '27', 'udpos': 'PUNCT', 'lemma': ';///_', 'head': '30', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
et
CCONJ
['et']
{'n': '28', 'udpos': 'CC

{'n': '26', 'udpos': 'ADP', 'lemma': 'de', 'head': '27', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
guyenne
PROPN
['guyenne']
{'n': '27', 'udpos': 'PROPN', 'lemma': 'guyenne', 'head': '22', 'function': 'conj', 'join': '_', 'retagging': 'PROPN'}
,
PUNCT
[',', '.', '_']
{'n': '28', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '30', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
d'
ADP
['de']
{'n': '29', 'udpos': 'ADP', 'lemma': 'de', 'head': '30', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
angou
PROPN
['anjou']
{'n': '30', 'udpos': 'PROPN', 'lemma': 'anjou', 'head': '24', 'function': 'conj', 'join': '_', 'retagging': 'PROPN'}
,
PUNCT
[',', '.', '_']
{'n': '31', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '34', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
et
CCONJ
['et']
{'n': '32', 'udpos': 'CCONJ', 'lemma': 'et', 'head': '34', 'function': 'cc', 'join': '_', 'retagging': 'CCONJ'}
du
ADP
['de+le']
{'n': '33', 'udpos': 'ADP', 'lemma': 'de+le',

['comme']
{'n': '5', 'udpos': 'SCONJ', 'lemma': 'comme', 'head': '7', 'function': 'mark', 'join': '_', 'retagging': 'SCONJ'}
il
PRON
['il']
{'n': '6', 'udpos': 'PRON', 'lemma': 'il', 'head': '7', 'function': 'nsubj', 'join': '_', 'retagging': 'PRON'}
partoit
VERB
['partir']
{'n': '7', 'udpos': 'VERB', 'lemma': 'partir', 'head': '10', 'function': 'advcl', 'join': '_', 'retagging': 'VERB'}
,
PUNCT
[',', '.', '_']
{'n': '8', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '7', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
lui
PRON
['il']
{'n': '9', 'udpos': 'PRON', 'lemma': 'il', 'head': '10', 'function': 'iobj', 'join': '_', 'retagging': 'PRON'}
vindrent
VERB
['venir']
{'n': '10', 'udpos': 'VERB', 'lemma': 'venir', 'head': '0', 'function': 'root', 'join': '_', 'retagging': 'VERB'}
les
DET
['le']
{'n': '11', 'udpos': 'DET', 'lemma': 'le', 'head': '12', 'function': 'det', 'join': '_', 'retagging': 'DET'}
nouvelles
NOUN
['nouveau', 'nouvelle']
{'n': '12', 'udpos': 'NOUN', 'lemma':

...

PUNCT
[',', '.', '_']
{'n': '34', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '37', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}

							
ADP
[]
{'n': '35', 'udpos': 'ADP', 'lemma': '_', 'head': '37', 'function': 'case', 'join': '_', 'retagging': 'ADP', 'NoMatchingPresto': 'Word'}
grant
ADJ
['grand']
{'n': '36', 'udpos': 'ADJ', 'lemma': 'grand', 'head': '37', 'function': 'amod', 'join': '_', 'retagging': 'ADJ'}
compagnie
NOUN
['compagne', 'compagnie']
{'n': '37', 'udpos': 'NOUN', 'lemma': 'compagne///compagnie', 'head': '44', 'function': 'obl', 'join': '_', 'retagging': 'NOUN'}
de
ADP
['de']
{'n': '38', 'udpos': 'ADP', 'lemma': 'de', 'head': '56', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
gens
NOUN
['gens', 'gent']
{'n': '39', 'udpos': 'NOUN', 'lemma': 'gens///gent', 'head': '37', 'function': 'nmod', 'join': '_', 'retagging': 'NOUN'}
,
PUNCT
[',', '.', '_']
{'n': '40', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '37', 'function': 'punct', 'join': '_', 'ret

ADP
['de']
{'n': '29', 'udpos': 'ADP', 'lemma': 'de', 'head': '30', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
nevers
PROPN
['nevers', 'névers']
{'n': '30', 'udpos': 'PROPN', 'lemma': 'nevers///névers', 'head': '27', 'function': 'conj', 'join': '_', 'retagging': 'PROPN'}
,
PUNCT
[',', '.', '_']
{'n': '31', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '33', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
d'
ADP
['de']
{'n': '32', 'udpos': 'ADP', 'lemma': 'de', 'head': '33', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
eu
PROPN
['év']
{'n': '33', 'udpos': 'PROPN', 'lemma': 'év', 'head': '27', 'function': 'conj', 'join': '_', 'retagging': 'PROPN'}
et
CCONJ
['et']
{'n': '34', 'udpos': 'CCONJ', 'lemma': 'et', 'head': '36', 'function': 'cc', 'join': '_', 'retagging': 'CCONJ'}
de
ADP
['de']
{'n': '35', 'udpos': 'ADP', 'lemma': 'de', 'head': '36', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
saint-pol
PROPN
['saint-paul']
{'n': '36', 'udpos': 'PROPN', 'lemm

{'n': '51', 'udpos': 'NOUN', 'lemma': 'mort', 'head': '47', 'function': 'obl', 'join': '_', 'retagging': 'NOUN'}
jehan
PROPN
['jean']
{'n': '52', 'udpos': 'PROPN', 'lemma': 'jean', 'head': '47', 'function': 'nsubj', 'join': '_', 'retagging': 'PROPN'}
monseigneur
NOUN
['monseigneur']
{'n': '53', 'udpos': 'NOUN', 'lemma': 'monseigneur', 'head': '52', 'function': 'flat', 'join': '_', 'retagging': 'NOUN'}
de
ADP
['de']
{'n': '54', 'udpos': 'ADP', 'lemma': 'de', 'head': '53', 'function': 'flat', 'join': '_', 'retagging': 'ADP'}
lorraine
PROPN
['lorraine', 'lorraîne']
{'n': '55', 'udpos': 'PROPN', 'lemma': 'lorraine///lorraîne', 'head': '53', 'function': 'flat', 'join': '_', 'retagging': 'PROPN'}
,
PUNCT
[',', '.', '_']
{'n': '56', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '59', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}

							
ADP
[]
{'n': '57', 'udpos': 'ADP', 'lemma': '_', 'head': '59', 'function': 'case', 'join': '_', 'retagging': 'ADP', 'NoMatchingPresto': 'Word'}
c

que
PRON
['que']
{'n': '5', 'udpos': 'PRON', 'lemma': 'que', 'head': '7', 'function': 'obj', 'join': '_', 'retagging': 'PRON'}
françois
PROPN
['françois']
{'n': '6', 'udpos': 'PROPN', 'lemma': 'françois', 'head': '7', 'function': 'nsubj', 'join': '_', 'retagging': 'PROPN'}
amenoient
VERB
['amener']
{'n': '7', 'udpos': 'VERB', 'lemma': 'amener', 'head': '4', 'function': 'acl:relcl', 'join': '_', 'retagging': 'VERB'}
fut
AUX
['être']
{'n': '8', 'udpos': 'AUX', 'lemma': 'être', 'head': '9', 'function': 'cop', 'join': '_', 'retagging': 'AUX'}
grant
ADJ
['grand']
{'n': '9', 'udpos': 'ADJ', 'lemma': 'grand', 'head': '0', 'function': 'root', 'join': '_', 'retagging': 'ADJ'}
;
PUNCT
[';', '_']
{'n': '10', 'udpos': 'PUNCT', 'lemma': ';///_', 'head': '9', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
par
ADP
['par']
{'n': '11', 'udpos': 'ADP', 'lemma': 'par', 'head': '12', 'function': 'case', 'join': '_', 'retagging': 'ADP'}
quoy
PRON
['que', 'quoi']
{'n': '12', 'udpos': 'PRON', 'lemma

{'n': '14', 'udpos': 'VERB', 'lemma': 'lever', 'head': '3', 'function': 'amod', 'join': '_', 'retagging': 'VERB'}
,
PUNCT
[',', '.', '_']
{'n': '15', 'udpos': 'PUNCT', 'lemma': ',///.///_', 'head': '17', 'function': 'punct', 'join': '_', 'retagging': 'PUNCT'}
le
DET
['le']
{'n': '16', 'udpos': 'DET', 'lemma': 'le', 'head': '17', 'function': 'det', 'join': '_', 'retagging': 'DET'}
temps
NOUN
['temps']
{'n': '17', 'udpos': 'NOUN', 'lemma': 'temps', 'head': '24', 'function': 'nsubj', 'join': '_', 'retagging': 'NOUN'}
estant
VERB
['ester', 'étendre', 'être']
{'n': '18', 'udpos': 'VERB', 'lemma': 'ester///étendre///être', 'head': '17', 'function': 'acl', 'join': '_', 'retagging': 'VERB'}
cler
ADJ
['clair']
{'n': '19', 'udpos': 'ADJ', 'lemma': 'clair', 'head': '17', 'function': 'amod', 'join': '_', 'retagging': 'ADJ'}
et
CCONJ
['et']
{'n': '20', 'udpos': 'CCONJ', 'lemma': 'et', 'head': '21', 'function': 'cc', 'join': '_', 'retagging': 'CCONJ'}
net
ADJ
['net']
{'n': '21', 'udpos': 'ADJ', 'lem

In [8]:
def indent(elem, level=0, more_sibs=False):
    i = "\n"
    if level:
        i += (level-1) * '\t'
    num_kids = len(elem)
    if num_kids:
        if not elem.text or not elem.text.strip():
            elem.text = i + "\t"
            if level:
                elem.text += '\t'
        count = 0
        for kid in elem:
            indent(kid, level+1, count < num_kids - 1)
            count += 1
        if not elem.tail or not elem.tail.strip():
            elem.tail = i
            if more_sibs:
                elem.tail += '\t'
    else:
        if level and (not elem.tail or not elem.tail.strip()):
            elem.tail = i
            if more_sibs:
                elem.tail += '\t'

In [9]:
ET.ElementTree(root).write(path_out, encoding="utf-8")
tree = ET.parse(open(path_out, encoding='utf-8'))
root = tree.getroot()
indent(root)
ET.ElementTree(root).write(path_out, encoding="utf-8")